In [1]:
from transformers import PhobertTokenizer, BertModel
import torch
import numpy as np

model_name = 'vinai/phobert-base-v2'
tokenizer = PhobertTokenizer.from_pretrained(model_name)
model = BertModel.from_pretrained(model_name)

# sentence = "This is an example sentence."
sentence = "Chúng_tôi là những nghiên_cứu_viên"
sentence = "Ông Nguyễn_Khắc_Chúc đang làm_việc tại Đại_học Quốc_gia Hà_Nội"
sentence = "bàn thắng Sang hiệp 2 , HLV Vũ_Hồng Việt yêu_cầu các học_trò tấn_công mạnh_mẽ hơn nữa , trong khi U16 Mông_Cổ có dấu_hiệu xuống sức rõ_rệt Những bàn thắng đến như một tất_yếu Riêng ở hiệp đấu này , Chí_Bảo đã ghi tới 4 bàn thắng , giúp U16 Việt_Nam thắng chung_cuộc 9 Như_vậy qua 2 trận đấu , U16 Việt_Nam toàn_thắng , ghi tới 14 bàn và để lọt_lưới 2 , hiệu_số bàn thắng_bại là 12 Tại bảng I lúc này , thầy_trò Vũ_Hồng Việt có cùng điểm_số như U16_Australia nhưng xếp dưới vì kém hiệu_số bàn thắng_bại"




2023-05-24 22:47:32.217402: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
You are using a model of type roberta to instantiate a model of type bert. This is not supported for all configurations of models and can yield errors.
Some weights of the model checkpoint at vinai/phobert-base-v2 were not used when initializing BertModel: ['roberta.encoder.layer.3.attention.self.value.bias', 'roberta.encoder.layer.11.output.LayerNorm.bias', 'roberta.encoder.layer.1.attention.output.LayerNorm.bias', 'roberta.encoder.layer.0.output.LayerNorm.bias', 'roberta.encoder.layer.1.output.LayerNorm.bias', 'roberta.encoder.layer

In [2]:
import json
create_ent_sent_json_file = False

def write_append_data_to_txt_file(full_path_to_file, txt):
    with open(full_path_to_file,'a') as out:
        out.write(f'{txt}\n')
        # out.write(f'{txt}')s
        
def clear_file(full_path_to_files_list):
    for _file in full_path_to_files_list:
      with open(_file,'w') as out:
        out.write(f'')

In [3]:


def reduce_emb_vec_org(vt1):
  
  vt1_np = vt1.detach().numpy()
  vt1_mean = vt1_np.reshape(-1, 4).mean(axis=1)
  return vt1_mean

def embedding_sent_to_dict_of_vector_word(sentence):
    # Tokenize the sentence
    tokens = tokenizer.tokenize(sentence)

    # Add the special tokens [CLS] and [SEP]
    tokens = ['[CLS]'] + tokens + ['[SEP]']

    # Convert tokens to input IDs and create attention mask
    input_ids = tokenizer.convert_tokens_to_ids(tokens)
    attention_mask = [1] * len(input_ids)

    # Convert lists to tensors
    input_ids = torch.tensor([input_ids])
    attention_mask = torch.tensor([attention_mask])

    # Generate the embeddings
    with torch.no_grad():
        outputs = model(input_ids, attention_mask=attention_mask)
        embeddings = outputs.last_hidden_state[0]

    # Create the word-to-embedding dictionary
    # word_embeddings_dict = {}
    # for i in range(1, len(tokens)-1):
    #     word = tokens[i]
    #     embedding = embeddings[i]
    #     word_embeddings_dict[word] = embedding
        

    # return word_embeddings_dict

    word_embeddingslist = []
    for i in range(1, len(tokens)-1):
        # word = tokens[i]
        # embedding = embeddings[i]
        # word_embeddings_dict[word] = embedding
        vector = embeddings[i]
        # print(vector.shape)
        vt_reduce = reduce_emb_vec_org(vector) 
        print(tokens[i] ,vt_reduce.shape)
        word_embeddingslist.append((tokens[i], vt_reduce))
    return word_embeddingslist


In [4]:
# sent = "bàn thắng Sang hiệp 2 , HLV Vũ_Hồng Việt yêu_cầu các học_trò tấn_công mạnh_mẽ hơn nữa , trong khi U16 Mông_Cổ có dấu_hiệu xuống sức rõ_rệt Những bàn thắng đến như một tất_yếu Riêng ở hiệp đấu này , Chí_Bảo đã ghi tới 4 bàn thắng , giúp U16 Việt_Nam thắng chung_cuộc 9 Như_vậy qua 2 trận đấu , U16 Việt_Nam toàn_thắng , ghi tới 14 bàn và để lọt_lưới 2 , hiệu_số bàn thắng_bại là 12 Tại bảng I lúc này , thầy_trò Vũ_Hồng Việt có cùng điểm_số như U16_Australia nhưng xếp dưới vì kém hiệu_số bàn thắng_bạ"
# sent = " HLV Vũ_Hồng Việt yêu_cầu các học_trò"
# eb = embedding_sent_to_dict_of_vector_word(sent)
# print(eb)



In [5]:
# sent = "bàn thắng Sang hiệp 2 , HLV Vũ_Hồng Việt yêu_cầu các học_trò tấn_công mạnh_mẽ hơn nữa , trong khi U16 Mông_Cổ có dấu_hiệu xuống sức rõ_rệt Những bàn thắng đến như một tất_yếu Riêng ở hiệp đấu này , Chí_Bảo đã ghi tới 4 bàn thắng , giúp U16 Việt_Nam thắng chung_cuộc 9 Như_vậy qua 2 trận đấu , U16 Việt_Nam toàn_thắng , ghi tới 14 bàn và để lọt_lưới 2 , hiệu_số bàn thắng_bại là 12 Tại bảng I lúc này , thầy_trò Vũ_Hồng Việt có cùng điểm_số như U16_Australia nhưng xếp dưới vì kém hiệu_số bàn thắng_bạ"
# eb = embedding_words_in_sents_full_shape(sent)


# print(eb)
already_embedded_set = set()
embedded_file = \
    "/Users/n2t2k/Documents/Studying/Master/Thesis/InProgress/Coding/ORIGIN_RUN_ALL_edge-oriented-graph-master-studying/dataProcessingOfficialCleaned/dev_processed/split_sentence_underthesea/code/BERT_merge_file/data/PubMed-VLSP_origin_after_processed.txt"
clear_file([embedded_file])

error_sent_embedded_file = \
    "/Users/n2t2k/Documents/Studying/Master/Thesis/InProgress/Coding/ORIGIN_RUN_ALL_edge-oriented-graph-master-studying/dataProcessingOfficialCleaned/dev_processed/split_sentence_underthesea/code/BERT_merge_file/BERT_create_corpus/view_data/data/error_sent_embedded_file.txt"
clear_file([error_sent_embedded_file])


out_all_sent = \
    "/Users/n2t2k/Documents/Studying/Master/Thesis/InProgress/Coding/ORIGIN_RUN_ALL_edge-oriented-graph-master-studying/dataProcessingOfficialCleaned/dev_processed/split_sentence_underthesea/code/BERT_merge_file/BERT_create_corpus/view_data/data/all_sent_to_wb.txt"
error_count = 0
total_sent = 0
with open(out_all_sent, 'r') as in_file:
    lines = in_file.readlines()
    for sent in lines:
        total_sent+=1
        sent = sent.replace("\n","")
        # sent = "7 nguyên_nhân khiến Real_Madrid bị Barcelona bỏ_xa tại La_Liga Tờ Marca của Tây Ban_Nha đã chỉ ra những yếu_tố lý_giải cho sự khởi_đầu tệ_hại của Real_Madrid tại La_Liga 20172018"
        try:
            emb_vec_reduce =  embedding_sent_to_dict_of_vector_word(sent.strip())
            # print(emb_vec_reduce)
            for tk, em_w in emb_vec_reduce:
                if tk in already_embedded_set:
                    continue
                already_embedded_set.add(tk)
                em_w_ls = em_w.tolist()
                em_w_ls = " ".join(map(str, em_w_ls))      
                write_append_data_to_txt_file(embedded_file, f"{tk} {em_w_ls}")
        except:
            error_count +=1
            write_append_data_to_txt_file(error_sent_embedded_file, sent)
        # break
        # if error_count == 1:
        #     break

print("already_embedded_set word: ", len(already_embedded_set))
print("total_sent: ", total_sent)
print("error_count sent: ", error_count)



Uber (192,)
bị (192,)
tước (192,)
giấy_phép (192,)
ở (192,)
London (192,)
Ứng_dụng (192,)
taxi (192,)
chiếm (192,)
1 (192,)
3 (192,)
số (192,)
xe (192,)
thuê (192,)
tư_nhân (192,)
với (192,)
hơn (192,)
40.000 (192,)
tài_xế (192,)
tại (192,)
thủ_đô (192,)
Anh (192,)
, (192,)
sẽ (192,)
bị (192,)
tước (192,)
giấy_phép (192,)
hoạt_động (192,)
từ (192,)
cuối (192,)
tháng (192,)
9 (192,)
này (192,)
Ngày (192,)
22 (192,)
- (192,)
9 (192,)
, (192,)
Sở_@@ (192,)
Giao@@ (192,)
_th@@ (192,)
ông_@@ (192,)
London (192,)
T@@ (192,)
f@@ (192,)
L (192,)
thông_báo (192,)
không (192,)
gia_hạn (192,)
giấy_phép (192,)
Uber (192,)
khi (192,)
hết (192,)
hạn (192,)
vào (192,)
ngày (192,)
30 (192,)
- (192,)
9 (192,)
vì (192,)
hoạt_động (192,)
của (192,)
Uber (192,)
gây (192,)
nguy_hiểm (192,)
cho (192,)
an_toàn (192,)
công_cộng (192,)
Uber (192,)
có (192,)
21 (192,)
ngày (192,)
để (192,)
khiếu_nại (192,)
và (192,)
có_thể (192,)
tiếp_tục (192,)
hoạt_động (192,)
đến (192,)
khi (192,)
quá_trình (192,)
kháng_cáo 